In [42]:
from bs4 import BeautifulSoup as bs
import requests
from tqdm import tqdm 
import json
import os
import datetime
import re
import csv
import time
import pandas as pd
from nltk.stem import *
from collections import Counter
from functools import reduce
import numpy as np

In [43]:
#TODO
#Download all the missing pages
#Create all the missing tsv
#Clean and comment the code
#CHECK EFFICIENCY 1.2 and 1.3
#Parse list before saving into

### 1. Data collection
## 1.1. Get the list of places

In [ ]:
total_link = []
s = requests.Session()
for n in tqdm(range(1,401)):
    url = f'https://www.atlasobscura.com/places?page={n}&sort=likes_count'
    result = s.get(url)
    soup = bs(result.text)
    puf = soup.find_all("a", {'class': 'content-card content-card-place'})
    for x in puf:
        total_link.append(x['href'])


In [ ]:
f = open('total_link.txt',"r")
total_link = f.read().split("\n")

## 1.2. Crawl places

In [ ]:
def downloadPage(start,end, array):
    count_link = ((start-1)*18)+1
    count_page = start
    
    parent_dir = f'./all_Pages'
    s = requests.Session()
    header = {'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'}
    for x in tqdm(range(start, end)):
        if count_link%10 == 0:
            s = requests.Session()
        if count_link%18 == 1:
            #directory = f'folder_{count_page}'
            path = os.path.join(parent_dir, f"folder_{count_page}")
            #os.remove(path)
            os.mkdir(path)
        for y in range(18):
            url = f'https://www.atlasobscura.com{array[count_link-1]}'
            name_file = f'location_{count_link}'
            name_folder = f'folder_{count_page}'
            with open(f'./all_Pages/{name_folder}/{name_file}.html', 'w', encoding='utf8') as fp:
                a = s.get(url, headers = header)
                fp.write(a.text)
                if a.status_code != 200:
                     time.sleep(120)
                     a = s.get(url, headers = header)
                fp.write(s.get(url).text)
            if count_link%18 == 0:
                count_page += 1
            count_link += 1
           
        

In [ ]:
arr = [47, 98, 89, 223, 56, 73,81, 307, 299, 182, 282, 198, 324, 215, 265, 173, 240, 190, 257, 383, 207, 316, 291, 249, 333, 358, 400, 374, 232, 349, 391, 274, 341]
arr = sorted(arr)
print(arr)

# for x in arr:
#     downloadPage(x, x+1, total_link)

## 1.3 Parse downloaded pages

In [ ]:


os.mkdir("TSV Files")
for x in os.listdir("all_Pages"):
    for y in os.listdir(f'all_Pages/{x}'):
        with open(f'./all_Pages/{x}/{y}', encoding='utf8') as f:
            p = f.read()
            soup =  bs(p)
            print(f"{x}/{y}")
            pageAttribute = []
            placeName = findPlaceName(soup)
            placeTags = findPlaceTags(soup)
            numPeopleVisited = findNumPeopleVisited(soup)
            numPeopleWant = findNumPeopleWant(soup)
            placeDesc = findDescription(soup)
            placeShortDesc = findShortDescription(soup)
            placeNearby = findNearbyPlaces(soup)
            placeAddress = findAddress(soup)
            placeAlt, placeLong = findCordinates(soup)
            placeEditors = findPostEditors(soup)
            placePubDate = findPublishingDate(soup)
            placeRelatedList = findPlaceNear(soup)
            placeRelatedPlaces = findRelatedPlaces(soup)
            placeURL = findPageURL(soup)
            with open(f'./TSV Files/{y[:-5]}.tvs', 'wt', encoding='utf8') as fp:
                tsv_writer = csv.writer(fp, delimiter='\t')
                tsv_writer.writerow([placeName, placeTags, numPeopleVisited, numPeopleWant, placeDesc, placeShortDesc, placeNearby, placeAddress, placeAlt, placeLong, placeEditors, placePubDate, placeRelatedList, placeRelatedPlaces, placeURL])
        

In [ ]:
def findPlaceName(soup):
    placeName = soup.find("h1", {"class": "DDPage__header-title"})
    if placeName != None:
        placeName = placeName.text
    #placeName = re.sub('[A-Za-z0-9_.,! "]*' ,'',placeName)
    return placeName

def findPlaceTags(soup):
    tags = []
    placeTags = soup.find_all("a", {"class": "itemTags__link js-item-tags-link"})
    for tag in placeTags:
        t = tag.text.replace("\n", "")
        #t = re.sub('[A-Za-z0-9 _.,!"]*','',t)
        tags.append(t)
    return tags

def findNumPeopleVisited(soup):
    peopleVisited = soup.find_all("div", {"class": "title-md item-action-count"})
    if len(peopleVisited) > 0:
        peopleVisited = int(peopleVisited[0].text)
    return peopleVisited

def findNumPeopleWant(soup):
    peopleVisited = soup.find_all("div", {"class": "title-md item-action-count"})
    if len(peopleVisited) > 0:
        peopleVisited = int(peopleVisited[1].text)
    return peopleVisited

def findDescription(soup):
    all_description = []
    descriptions = soup.find_all("div", {"class": "DDP__body-copy"})
    for description in descriptions:
        d = description.text.replace("\n","")
        all_description.append(d)
    return all_description

def findShortDescription(soup):
    shortDescription = soup.find("h3", {"class": "DDPage__header-dek"})
    if shortDescription != None:
        shortDescription = shortDescription.text.replace("\n", "")
    return shortDescription

def findNearbyPlaces(soup):
    nearPlaces = []
    nearbyPlaces = soup.find_all("div", {"class": "DDPageSiderailRecirc__item-title"})
    if nearbyPlaces != None:
        for place in nearbyPlaces:
            p = place.text.replace("\n","")
            nearPlaces.append(p)
        #Convert the list to set, and then back again to list to remove repetition
    return list(set(nearPlaces))

def findAddress(soup):
    strings = []
    adress_strings = soup.find("address", {"class": "DDPageSiderail__address"})
    if adress_strings != None:
        adress_strings = adress_strings.find("div")
        for info in adress_strings:
            s = info.text.replace("\n", "")
            if s != "":
                strings.append(s)
        if len(strings) > 3:
            return " ".join(strings[:3])
    else:
        return " "

def findCordinates(soup):

    cordinates = soup.find("div", {"class":"DDPageSiderail__coordinates js-copy-coordinates"})
    if cordinates != None:
        return cordinates.text.replace("\n", "").replace(" ","").split(",")
    return " ", " "

def findPostEditors(soup):
    all_editors =[]
    editors = soup.find_all("a", {"class":"DDPContributorsList__contributor"})         
    for person in editors:
        s = person.text.replace("\n", "")
        all_editors.append(s)
    return all_editors

def findPublishingDate(soup):
    #Pick the right info
    dateString = soup.find("div", {"class":"DDPContributor__name"}) 
    #Let's clean the string
    s = dateString.text.replace("\n", "")
    #Let's modify it for the right format of datetime
    split = s.split()
    #Let's convert the string Month into the corrispondent number by using "strptime()" 
    split[0] = str(datetime.datetime.strptime(split[0], '%B').month)
    #My format
    format = "%m %d, %Y"
    #Convert from String to datetime
    date = datetime.datetime.strptime(" ".join(split), format)
    return date

def findPlaceNear(soup):
    lists =[]
    relatedLists = soup.find("div", {"data-gtm-template":"DDP Footer Recirc Nearby"})
    if relatedLists != None:
        relatedLists = relatedLists.find_all("h3", {"class":"Card__heading --content-card-v2-title js-title-content"})
        for list in relatedLists:
            s = list.text.replace("\n", "")
            #s = re.sub('[A-Za-z0-9 _.,!"]*','',s)
            lists.append(s)
    return lists

def findRelatedPlaces(soup):
    lists =[]
    relatedLists = soup.find("div", {"data-gtm-template":"DDP Footer Recirc Related"})
    if relatedLists != None:
        relatedLists = relatedLists.find_all("h3", {"class":"Card__heading --content-card-v2-title js-title-content"})
        for list in relatedLists:
            s = list.text.replace("\n", "")
            #s = re.sub('[A-Za-z0-9 _.,!"]*','',s)
            lists.append(s)
    return lists

def findPageURL(soup):
    numVisitedPeople = soup.find("link", {"rel":"canonical"})
    return numVisitedPeople['href']



## Load all the tsv file into one pandas dataframe

In [1]:

def load_tsv():
    tsv = []
    dtypes = {}
    for x in os.listdir("TSV Files"):
        df = pd.read_csv(f'TSV Files/{x}',
            sep="\t",
            header=None,
            names=["placeName", "placeTags", "numPeopleVisited", "numPeopleWant", "placeDesc", "placeShortDesc", "placeNearby","placeAdress", "placeAlt", "placeLong", "placeEditors","placePubDate", "placeRelatedList", "placeRelatedPlace", "placeURL"])
        tsv.append(df)

    return pd.concat(tsv)

In [4]:
data = load_tsv()


In [5]:
#Reset Index
data.reset_index(inplace = True)
data = data.drop(["index"], axis = 1)
data.head()


placeName                                          placeTags  \
0    City Hall Station  ['subways', 'subterranean', 'infrastructure', ...   
1          Dream House  ['optical oddities', 'eccentric homes', 'music...   
2  The Museum of Death  ['crime and punishment', 'memento mori', 'deat...   
3   God's Own Junkyard            ['neon', 'signs', 'collections', 'art']   
4   The Last Bookstore  ['bookstores', 'repositories of knowledge', 'b...   

   numPeopleVisited  numPeopleWant  \
0              1834           8603   
1               765           6007   
2              1761           5832   
3               856           5812   
4              3614           5816   

                                           placeDesc  \
0  ['The first New York City subway was built and...   
1  ['When walking down Church Street in Tribeca, ...   
2  ['The Museum of Death, a showcase of just that...   
3  ['For years, Walthamstow was known as an unrem...   
4  ['More than a few bibliophiles would prefer th...   

                                      placeShortDesc  \
0  A beautiful and abandoned New York subway stat...   
1  La Monte Young and Marian Zazeela's "Dream Hou...   
2  World's largest collection of serial killer ar...   
3  A kaleidoscopic warehouse-maze of handmade neo...   
4  This iconic L.A. bookshop is housed in an aban...   

                                         placeNearby  \
0  ['African Burial Ground National Monument', 'T...   
1  ['Aretha Franklin Subway Tributes', "The 'Ghos...   
2  ['Capitol Records Building Morse Code', 'Gower...   
3  ['The Ancient House', 'Walthamstow Market', 'T...   
4  ['Biddy Mason Memorial Park', 'Bradbury Buildi...   

                                         placeAdress  placeAlt  placeLong  \
0  31 Centre St New York, New York, 10007 United ...   40.7134   -74.0046   
1  275 Church St New York, New York, 10013 United...   40.7185   -74.0048   
2  6031 Hollywood Blvd. Los Angeles, California, ...   34.1017  -118.3212   
3    82A Shernhall St London, England United Kingdom   51.5839    -0.0083   
4  453 S. Spring St. Los Angeles, California, 900...   34.0477  -118.2494   

                                        placeEditors         placePubDate  \
0  ['Rebekah Otto', 'Annetta Black', 'Allan', 'ch...  2010-05-08 00:00:00   
1  ['seanmattison', 'mbison', 'Gray', 'Sofy', 'er...  2009-09-22 00:00:00   
2  ['Genki', 'hana', 'Lauren Levesque', 'britbarb...  2010-08-09 00:00:00   
3  ['FrustratedFormerContributor', 'ryanswift', '...  2017-04-18 00:00:00   
4  ['kcmick', 'paulruta', 'Avoiding Regret', 'Jes...  2013-02-27 00:00:00   

                                    placeRelatedList  \
0  ['African Burial Ground National Monument', 'T...   
1  ['Aretha Franklin Subway Tributes', 'Farm.One'...   
2  ['Hollywood Tower Apartments', 'Capitol Record...   
3  ['The Ancient House', 'The Bremer Car', 'Walth...   
4  ['Biddy Mason Memorial Park', 'Bradbury Buildi...   

                                   placeRelatedPlace  \
0  ['Crystal Palace Subway', 'Moscow Metro Statio...   
1  ['Callejon de Hamel', 'Casa Neverlandia', 'Cas...   
2  ['Museum Tot Zover', ' Roman Urn Collection at...   
3  ['Ignite Sign Art Museum', 'Buchstabenmuseum '...   
4  ['Alabama Booksmith', 'Book Corner', 'John K. ...   

                                            placeURL  
0  https://www.atlasobscura.com/places/city-hall-...  
1    https://www.atlasobscura.com/places/dream-house  
2  https://www.atlasobscura.com/places/the-museum...  
3  https://www.atlasobscura.com/places/gods-own-j...  
4  https://www.atlasobscura.com/places/last-books...

In [11]:

def stem_text(txt):
    return [word for word in txt.split(" ")]

## 2.1 

In [67]:
#The first dictionary where every key is a word and it's value is the corrispondant number to that word

def createFirstDic(data):
    dic = {}
    value = 1
    for description in data["placeDesc"]:
        description = description.replace('\'',"")
        description = description.replace('[',"")
        description = description.replace(']',"")
        for word in description.split():
            if word in dic.keys():
                continue
            else:
                dic[word] = value
                value += 1
    return dic

In [68]:
dic1 = createFirstDic(data)

In [69]:
dic1

{'The': 1,
 'first': 2,
 'New': 3,
 'York': 4,
 'City': 5,
 'subway': 6,
 'was': 7,
 'built': 8,
 'and': 9,
 'operated': 10,
 'by': 11,
 'the': 12,
 'Interborough': 13,
 'Rapid': 14,
 'Transit': 15,
 'Company': 16,
 '(IRT)': 17,
 'opened': 18,
 'on': 19,
 'October': 20,
 '27,': 21,
 '1904,': 22,
 'to': 23,
 'joy': 24,
 'of': 25,
 'elevated': 26,
 'train': 27,
 'streetcar': 28,
 'riders.The': 29,
 'Hall': 30,
 'station': 31,
 'IRT': 32,
 'local': 33,
 'track': 34,
 'lavished': 35,
 'with': 36,
 'fine': 37,
 'architectural': 38,
 'details,': 39,
 'including': 40,
 'glass': 41,
 'tiles': 42,
 'large': 43,
 'chandeliers.': 44,
 'However,': 45,
 'Gustavino': 46,
 'vaulted': 47,
 'ceilings': 48,
 'skylights': 49,
 'were': 50,
 'lost': 51,
 'busy': 52,
 'commuters,': 53,
 'stop': 54,
 'one': 55,
 'least-used': 56,
 'in': 57,
 'system.': 58,
 'It': 59,
 'only': 60,
 'that': 61,
 'did': 62,
 'not': 63,
 'have': 64,
 'turnstiles': 65,
 'installed': 66,
 '1923,': 67,
 'nearby': 68,
 'Brooklyn': 6

In [143]:
def createSecondDic(data, dic1):
    dic2 = {}
    a = 0
    for description in data["placeDesc"]:
        description = description.replace('\'',"")
        description = description.replace('[',"")
        description = description.replace(']',"")
        for word in description.split():
            if dic1[word] in dic2.keys():
                dic2[dic1[word]].add(data.placeName[a])
            else:
                b = []
                dic2[dic1[word]] = set([data.placeName[a]])
            # print(dic2)
        a += 1
    return dic2

    

In [144]:
dic2 = createSecondDic(data,dic1)

In [145]:
dic2

{1: {'Fallingwater',
  'The Dark Hedges',
  "Devil's Hole",
  'Musical Parking Garage',
  'Helios House',
  'Great Wall of Los Angeles',
  'Shade Swamp Sanctuary',
  'Vote Against Prohibition Sign',
  'Gibsonton, Florida',
  'Berkeley Springs Castle',
  "The Witches' Well ",
  'Combine City',
  'The Mail Rail',
  'Giant Prairie Dog',
  'Salt & Pepper Shaker Museum',
  'The Sherlock Holmes Museum',
  'Kungsträdgården Metro Station',
  'Massacre Cave',
  'Laurel Dinosaur Park',
  'The Rainbow Tunnel',
  'Hubertusbad',
  'Showa Daibutsu: The Great Showa Buddha of Seiryuji',
  'Valley View Hot Springs',
  'Niagara Falls Whirlpool Aero Car',
  'Salt Ponds of San Francisco Bay',
  'Lake Chargoggagoggmanchauggagoggchaubunagungamaugg',
  'Earl Young Gnome Houses',
  "St Bride's Church & Charnel House",
  'Mound of the Hostages',
  'Studiolo Francesco I de’ Medici',
  'The 606 aka Bloomingdale Trail',
  'Amityville Horror House',
  'Museum of Fond Memories at Reed Books ',
  'Ruby Falls',
  "Si

In [95]:
data.placeName[3]

"God's Own Junkyard"

## 2.1 Execute the query

In [152]:
def query(list):
    s = dic2[dic1[list[0]]]
    for x in range(1, len(list)):
        s.intersection(dic2[dic1[list[x]]])
    return s

In [157]:
s = query(["class", "including"])

prova = data[data['placeName'].isin(list(s))]

In [158]:
prova.head()

placeName  \
94   Museum of Health and Medical Science   
371         The Sutro Egyptian Collection   
677                          Carousel Bar   
839                        Sylvan Terrace   
871                Salt River Wild Horses   

                                             placeTags  numPeopleVisited  \
94   ['anatomy museums', 'medical museums', 'museums']               503   
371  ['egyptian collections', 'obscura day location...               125   
677  ['carousels', 'machines', 'bars', 'hotels', 'U...              1297   
839                      ['natural wonders', 'nature']               317   
871  ['wild west', 'horses', 'deserts', 'rivers', '...               353   

     numPeopleWant                                          placeDesc  \
94            1029  ['This Houston museum features a 27’’½-foot in...   
371            955  ['The Sutro Collection of Egyptian Antiquities...   
677           2497  ['The Carousel Bar in Hotel Monteleone is the ...   
839            858  ['Now a residential street and popular film se...   
871            850  ['Wild horses running freely beneath a great, ...   

                                        placeShortDesc  \
94   A health museum containing a 27’’½-foot intest...   
371  Tenacious mummies survived dental problems, et...   
677  The only rotating bar in New Orleans has been ...   
839  A discreet little stairway on St. Nicholas Ave...   
871  These free-roaming horses were once destined t...   

                                           placeNearby  \
94   ['Twilight Epiphany Skyspace', 'Rothko Chapel'...   
371  ['Urbano Sundial', 'Broderick-Terry Duel Site'...   
677  ["'Birthplace of Dixie' Plaque", "Jean Lafitte...   
839  ['The Last Remnants of the Polo Grounds ', 'Ch...   
871  ['The Superstition Mountain Museum', 'Robert M...   

                                           placeAdress  placeAlt  placeLong  \
94   1515 Hermann Drive Houston, Texas, 77004 Unite...   29.7217   -95.3859   
371  1600 Holloway Avenue San Francisco, California...   37.7227  -122.4801   
677  214 Royal St New Orleans, Louisiana United States   29.9543   -90.0679   
839  Sylvan Terrace  New York, New York, 10032 Unit...   40.8349   -73.9399   
871     13020 Bush Highway Mesa, Arizona United States   33.5617  -111.5359   

                                          placeEditors         placePubDate  \
94   ['mbison', 'thegenxjourney', 'Thewanderingmeat...  2008-11-21 00:00:00   
371  ['littlebrumble', 'mbison', 'Annetta Black', '...  2011-03-16 00:00:00   
677  ['Tony Dunnell', 'wolfey63', 'cait7911', 'emot...  2018-08-13 00:00:00   
839          ['michelleferlito', 'Rachel', 'dlc31723']  2013-08-13 00:00:00   
871                       ['jdurand26', 'mrankin1975']  2018-07-16 00:00:00   

                                      placeRelatedList  \
94   ['Destination Mound Town (Hermann Park Train T...   
371  ['Urbano Sundial', 'Gregangelo Museum', 'Brode...   
677  ["'Birthplace of Dixie' Plaque", 'The Art of D...   
839  ['The Morris-Jumel Mansion', 'The Last Remnant...   
871  ['The Superstition Mountain Museum', 'Organ St...   

                                     placeRelatedPlace  \
94   ['Museo de Anatomopatología (Museum of Patholo...   
371  ['Egyptian Museum of Turin ', 'The Mummy Ankhe...   
677  ['Elliott Street Deli & Pub', 'Velvet', 'Chown...   
839  ['Barron Canyon Trail', 'Chickasaw National Re...   
871  ['Wild Horses of Shannon County ', 'Sudd Wetla...   

                                              placeURL  
94   https://www.atlasobscura.com/places/museum-hea...  
371  https://www.atlasobscura.com/places/sutro-egyp...  
677   https://www.atlasobscura.com/places/carousel-bar  
839  https://www.atlasobscura.com/places/sylvan-ter...  
871  https://www.atlasobscura.com/places/salt-river...